In [11]:
# pip install cowsay


SyntaxError: invalid syntax (<ipython-input-11-af49b7c7b8c7>, line 2)

In [12]:
import cowsay

import pandas as pd
import numpy
import sys
import nltk
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
nltk.download('stopwords')
from keras.models import Sequential
from keras.layers import Dense, Dropout, LSTM
from keras.utils import np_utils
from keras.callbacks import ModelCheckpoint

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ajrfl\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
Using TensorFlow backend.


In [16]:
file = pd.read_csv("Resources/DisneylandReviews.csv", encoding='ISO-8859-1')
file

Review_ID  Rating Year_Month     Reviewer_Location  \
0      670772142       4     2019-4             Australia   
1      670682799       4     2019-5           Philippines   
2      670623270       4     2019-4  United Arab Emirates   
3      670607911       4     2019-4             Australia   
4      670607296       4     2019-4        United Kingdom   
...          ...     ...        ...                   ...   
42651    1765031       5    missing        United Kingdom   
42652    1659553       5    missing                Canada   
42653    1645894       5    missing          South Africa   
42654    1618637       4    missing         United States   
42655    1536786       4    missing        United Kingdom   

                                             Review_Text               Branch  
0      If you've ever been to Disneyland anywhere you...  Disneyland_HongKong  
1      Its been a while since d last time we visit HK...  Disneyland_HongKong  
2      Thanks God it wasn   t too hot or too humid wh...  Disneyland_HongKong  
3      HK Disneyland is a great compact park. Unfortu...  Disneyland_HongKong  
4      the location is not in the city, took around 1...  Disneyland_HongKong  
...                                                  ...                  ...  
42651  i went to disneyland paris in july 03 and thou...     Disneyland_Paris  
42652  2 adults and 1 child of 11 visited Disneyland ...     Disneyland_Paris  
42653  My eleven year old daughter and myself went to...     Disneyland_Paris  
42654  This hotel, part of the Disneyland Paris compl...     Disneyland_Paris  
42655  I went to the Disneyparis resort, in 1996, wit...     Disneyland_Paris  

[42656 rows x 6 columns]

In [17]:
text = file["Review_Text"]
text

0        If you've ever been to Disneyland anywhere you...
1        Its been a while since d last time we visit HK...
2        Thanks God it wasn   t too hot or too humid wh...
3        HK Disneyland is a great compact park. Unfortu...
4        the location is not in the city, took around 1...
                               ...                        
42651    i went to disneyland paris in july 03 and thou...
42652    2 adults and 1 child of 11 visited Disneyland ...
42653    My eleven year old daughter and myself went to...
42654    This hotel, part of the Disneyland Paris compl...
42655    I went to the Disneyparis resort, in 1996, wit...
Name: Review_Text, Length: 42656, dtype: object

In [18]:
#Dataframe series needs to be converted to string for later steps to process
corpus = text.to_string()
corpus

"0        If you've ever been to Disneyland anywhere you...\n1        Its been a while since d last time we visit HK...\n2        Thanks God it wasn   t too hot or too humid wh...\n3        HK Disneyland is a great compact park. Unfortu...\n4        the location is not in the city, took around 1...\n5        Have been to Disney World, Disneyland Anaheim ...\n6        Great place! Your day will go by and you won't...\n7        Think of it as an intro to Disney magic for th...\n8        Feel so let down with this place,the Disneylan...\n9        I can go on talking about Disneyland. Whatever...\n10       Disneyland never cease to amaze me! I've been ...\n11       We spent the day here with our grown kids and ...\n12       We spend two days, the second day went early t...\n13       It was indeed the happiest place on earth! My ...\n14       This place is HUGE! Definately need more than ...\n15       We brought tickets before we left and got 2 da...\n16       Its huge , not enough to visit

In [19]:
#Creates tokenization function and defines parameters to optimize processing
def tokenize_words(input):
    # lowercase everything to standardize it
    input = input.lower()

    tokenizer = RegexpTokenizer(r'\w+')
    tokens = tokenizer.tokenize(input)

    # if the created token isn't in the stop words, make it part of "filtered"
    # filtered = filter(lambda token: token not in stopwords.words('english'), tokens)
    return " ".join(tokens)

In [20]:
input = tokenize_words(corpus)
input

'0 if you ve ever been to disneyland anywhere you 1 its been a while since d last time we visit hk 2 thanks god it wasn t too hot or too humid wh 3 hk disneyland is a great compact park unfortu 4 the location is not in the city took around 1 5 have been to disney world disneyland anaheim 6 great place your day will go by and you won t 7 think of it as an intro to disney magic for th 8 feel so let down with this place the disneylan 9 i can go on talking about disneyland whatever 10 disneyland never cease to amaze me i ve been 11 we spent the day here with our grown kids and 12 we spend two days the second day went early t 13 it was indeed the happiest place on earth my 14 this place is huge definately need more than 15 we brought tickets before we left and got 2 da 16 its huge not enough to visit in one day we 17 around 60 per person and if you want to eat 18 it s disneyland it just does not need revie 19 there is nothing more to say except that you b 20 we bought a 2 day tourist ticket

In [22]:
chars = sorted(list(set(input)))
char_to_num = dict((c, i) for i, c in enumerate(chars))

In [23]:
input_len = len(input)
vocab_len = len(chars)
print ("Total number of characters:", input_len)
print ("Total vocab:", vocab_len)

Total number of characters: 2207655
Total vocab: 37


In [24]:
seq_length = 50
x_data = []
y_data = []

In [25]:
for i in range(0, input_len - seq_length, 1):
    in_seq =input[i:i + seq_length]
    out_seq = input[i + seq_length]
    
    x_data.append([char_to_num[char] for char in in_seq])
    y_data.append(char_to_num[out_seq])

In [27]:
n_patterns = len(x_data)
print ("Total Patterns:", n_patterns)


Total Patterns: 2207605


In [28]:
X = numpy.reshape(x_data, (n_patterns, seq_length, 1))
X = X/float(vocab_len)
X

array([[[0.02702703],
        [0.        ],
        [0.51351351],
        ...,
        [0.83783784],
        [0.        ],
        [0.05405405]],

       [[0.        ],
        [0.51351351],
        [0.43243243],
        ...,
        [0.        ],
        [0.05405405],
        [0.        ]],

       [[0.51351351],
        [0.43243243],
        [0.        ],
        ...,
        [0.05405405],
        [0.        ],
        [0.51351351]],

       ...,

       [[0.7027027 ],
        [0.59459459],
        [0.        ],
        ...,
        [0.27027027],
        [0.18918919],
        [0.        ]],

       [[0.59459459],
        [0.        ],
        [0.13513514],
        ...,
        [0.18918919],
        [0.        ],
        [0.89189189]],

       [[0.        ],
        [0.13513514],
        [0.08108108],
        ...,
        [0.        ],
        [0.89189189],
        [0.51351351]]])

In [29]:
y = np_utils.to_categorical(y_data)
y

array([[1., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [30]:
#Build LSTM model
model = Sequential()
model.add(LSTM(256, input_shape=(X.shape[1], X.shape[2]), return_sequences=True))
model.add(Dropout(0.2))
model.add(LSTM(256, return_sequences=True))
model.add(Dropout(0.2))
model.add(LSTM(128))
model.add(Dropout(0.2))
model.add(Dense(y.shape[1], activation='softmax'))

In [31]:
#imports previously trained model weights into LSTM model
filename = "Resources/full_model_weights_final.hdf5"
model.load_weights(filename)
model.compile(loss='categorical_crossentropy', optimizer='adam')

In [32]:
num_to_char = dict((i, c) for i, c in enumerate(chars))

In [48]:
start = numpy.random.randint(0, len(x_data) - 1)
pattern = x_data[start]
print("Random Seed:")
text = ("\"", ''.join([num_to_char[value] for value in pattern]), "\"")
cowsay.cow(text)
start

Random Seed:
  _________________________________________________
 /                                                 \
| ('"', 'ead and so 28356 a must do world of colour |
| is spec', '"')                                    |
 \                                                 /
                                                      \
                                                       \
                                                         ^__^                             
                                                         (oo)\_______                   
                                                         (__)\       )\/\             
                                                             ||----w |           
                                                             ||     ||  
                                                             
                                                             


1462948